# Instability Analysis

In [1]:
# Load the necessary packages

import pandas as pd 
import numpy as np 
# import seaborn as sns
# import matplotlib.pyplot as plt
# from sklearn.preprocessing import StandardScaler
# import pyreadr
# import pingouin as pg
# from scipy import stats

In [ ]:
# Read in the .csv file of you mvalues. Make sure CG's are in the rows and sample names are in the columns
mvals = pd.read_csv("/Users/jenkinslab/Desktop/FAZSTProject/1500_mvals.csv",header=0,index_col=0)
mvals.iloc[:5,:]

In [6]:
#Subsetting certain columns

comet = ["X10367","X60039","X11011","X10822","X50130","X30135","X10410","X20176","X60048","X10200","X70048","X30197","X11309","X50046","X10595","X50132","X10291","X10482","X10139","X10533","X10487","X10147","X10129","X10926","X30179","X20226","X11053","X10356","X10375","X50237","X20234","X70005","X11473","X11168","X30200","X10645","X10452","X10851","X10206","X10660","X10852","X30171","X11165","X10148","X11210","X30095","X11095","X11124","X50228","X10587","X10173","X11453","X30146","X11013","X20047","X11494","X70021","X10770","X11012","X50143","X11106","X10874","X20071","X10380","X11090","X10142","X10254","X10548","X11123","X10151","X10035","X50001","X20017","X10279","X11147","X10123","X30007","X20061","X30224","X30236","X30185","X10519","X10351","X30058","X10540","X10478","X10300","X11102","X20219","X10878","X20131","X40029","X11093","X11241","X50211","X11249","X10441","X10238","X50216","X20104"]

mvalscomet = mvals.loc[:,comet]

mvalscomet.to_csv("/Users/jenkinslab/Desktop/FAZSTProject/DNA_Damage_Project/Instability/mvalscomet.csv")


In [3]:
# Read in the gene info data frame. Contains a list of CpG's and what promoter regions they overlap with. 
gene_info = pd.read_csv("/Users/jenkinslab/Desktop/Jenkins_Lab_Github/Instability_Code-main/gene_promoter_results_new_EPIC.tsv",sep='\t',header=0)
gene_info.iloc[:4,:]

CHR      START       STOP          CG  GENE
0   chr9  117903983  117903984  cg16682686  DEC1
1   chr9  117905075  117905076  cg04761824  DEC1
2   chr9  117903424  117903425  cg26981881  DEC1
3  chr19   58857257   58857258  cg27481534  A1BG

In [4]:
# Read in the cutoffs file. This has the cutoffs for each promoter region that we used donor samples to generate.
cutoffs_5=pd.read_csv("/Users/jenkinslab/Desktop/Jenkins_Lab_Github/Instability_Code-main/sperm_instability_cutoffs.csv",header=0,index_col=0)
cutoffs_5.iloc[:]

Mean_of_std  std_of_std  std3_of_std  Combined
SNORD115-20     0.270358    0.065962     0.197887  0.468245
SCOC            0.241969    0.081357     0.244071  0.486039
HAUS7           0.253154    0.081418     0.244255  0.497409
MIR33A          0.293159    0.068130     0.204389  0.497548
PARVG           0.372938    0.044834     0.134501  0.507439
...                  ...         ...          ...       ...
SLMAP           0.503496    0.155243     0.465728  0.969223
FXYD2           0.681426    0.095945     0.287835  0.969261
FXYD6-FXYD2     0.681426    0.095945     0.287835  0.969261
C9orf43         0.730631    0.079565     0.238696  0.969327
MIR4738         0.663197    0.102185     0.306556  0.969753

[1234 rows x 4 columns]

### NOTICE: After this point you shouldn't need to change the code

In [8]:
# Convert the gene promoter dataframe into a more readable dictionary
result = {}
count = 0

for index in gene_info.index:
    key = gene_info.iloc[index,4]
    value = gene_info.iloc[index,3]

    if key not in result:
        result[key] = [value]
    else:    
        result[key].append(value)

# Subset dictionary for the promoter regions that have 5 or more CpG's located in the promoter region
result_5 = {}
for key in result:
    new_length = len(result[key])
    if new_length >= 5:
        result_5[key] = result[key]
print("5+:",len(result_5))
# result_5.iloc[:]

5+: 12339


In [11]:
# Takes the standard deviation for all samples at each promoter. We will then compare these to our training_cutoffs
instability_df = pd.DataFrame()
count = 0
for key in result_5:
    count += 1
    beta_key = mvals.loc[result[key],:]
    instability_df[key] = (np.std(beta_key))
    # print("Finished", count, "/", len(result_5))
instability_df = instability_df.loc[:,cutoffs_5.index]
instability_df.iloc[:]

/var/folders/zg/syv6h0t100jg9zg1v37mf4nr0000gn/T/ipykernel_23154/2118012555.py:7: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  instability_df[key] = (np.std(beta_key))
/var/folders/zg/syv6h0t100jg9zg1v37mf4nr0000gn/T/ipykernel_23154/2118012555.py:7: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  instability_df[key] = (np.std(beta_key))
/var/folders/zg/syv6h0t100jg9zg1v37mf4nr0000gn/T/ipykernel_23154/2118012555.py:7: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many tim

SNORD115-20      SCOC     HAUS7    MIR33A     PARVG      CST8  \
X10007     0.336933  0.245190  0.198394  0.227964  0.335712  0.377430   
X10011     0.441479  0.212522  0.334728  0.231836  0.347639  1.422094   
X10052     0.388682  0.317492  0.242302  0.421431  0.422223  0.248379   
X10091     0.253991  0.345034  0.702109  0.325877  0.263447  0.211302   
X10125     0.386634  0.530486  0.465273  0.398656  0.325160  0.508176   
...             ...       ...       ...       ...       ...       ...   
X50214     0.500680  0.319585  0.398352  0.243510  0.242959  0.335815   
X50217     0.623849  0.900755  1.078242  0.191524  0.428961  0.357261   
X11479     0.495777  0.722531  0.930420  0.532842  0.268683  0.401607   
X11392     0.284977  0.315580  0.202897  0.369034  0.348382  0.248616   
X11426     0.482163  0.673613  0.545651  0.175934  0.458693  0.218528   

            GPD1    ADGRG3    TAS2R5   UBASH3A  ...     CCM2L    NKX2-3  \
X10007  0.275460  0.264622  0.292495  0.255391  ...  0.802107  0.611416   
X10011  0.392539  0.441807  0.295832  0.301038  ...  0.626883  0.667559   
X10052  0.233920  0.564257  0.310257  0.287147  ...  0.795853  0.626510   
X10091  0.439021  0.364778  0.483691  0.291884  ...  0.530533  0.669548   
X10125  0.369958  0.333346  0.466845  0.527634  ...  0.749523  0.871713   
...          ...       ...       ...       ...  ...       ...       ...   
X50214  0.382441  0.602570  0.363223  0.268041  ...  1.011804  0.702298   
X50217  0.925247  0.870555  0.107204  0.959805  ...  0.884261  0.869718   
X11479  1.193919  0.799697  0.470375  0.713022  ...  1.223961  1.045891   
X11392  0.250707  0.564938  0.313710  0.270581  ...  1.029934  1.053688   
X11426  1.129264  0.916191  0.331109  0.526543  ...  1.253366  0.962929   

         SULT1C4  LOC643072      ECI1     SLMAP     FXYD2  FXYD6-FXYD2  \
X10007  0.474981   0.543723  0.608725  0.591175  0.578441     0.578441   
X10011  0.576625   0.584500  0.625336  0.474116  0.640182     0.640182   
X10052  0.989375   0.562771  0.482773  0.539268  0.596988     0.596988   
X10091  1.140562   0.505251  0.977601  1.040372  0.922179     0.922179   
X10125  0.615179   0.762791  0.509960  0.667107  0.591927     0.591927   
...          ...        ...       ...       ...       ...          ...   
X50214  1.125584   0.451928  0.702873  1.260224  0.647652     0.647652   
X50217  1.915819   0.552030  0.594074  2.539496  0.598135     0.598135   
X11479  1.649302   0.775130  0.869535  2.008451  0.674444     0.674444   
X11392  1.315222   0.620334  0.379753  0.750961  0.572327     0.572327   
X11426  1.537696   0.549105  0.562662  1.404157  0.672084     0.672084   

         C9orf43   MIR4738  
X10007  0.744822  0.595503  
X10011  0.593098  0.641894  
X10052  0.800158  0.626460  
X10091  0.791119  0.752453  
X10125  0.772025  0.391161  
...          ...       ...  
X50214  0.755026  1.253517  
X50217  0.709538  1.691228  
X11479  0.914239  1.331613  
X11392  0.488404  0.849179  
X11426  0.708424  1.398914  

[103 rows x 1234 columns]

In [13]:
# Calculating Chaos Score and total variance score
chaos_scores_df = pd.DataFrame(columns=['Sentrix_ID','Chaos_Score'])
total_variance_df = pd.DataFrame(columns=['Sentrix_ID','Total_Variance'])
for sentrix_id in  instability_df.index:
    total_variance = []
    count = 0
    for promoter in instability_df.columns:
        sample = instability_df.loc[sentrix_id,promoter]
        cutoff_3 = cutoffs_5.loc[promoter,"Combined"]
        cutoff_3 = cutoff_3 * 1
        if sample > cutoff_3:
            variance = (sample - cutoff_3)
            total_variance.append(variance)
            count += 1
    total_variance = np.sum(total_variance)
    df2 = {'Sentrix_ID': sentrix_id, 'Chaos_Score': count}
    df3 = {'Sentrix_ID': sentrix_id, 'Total_Variance': total_variance}
    chaos_scores_df = chaos_scores_df.append(df2, ignore_index=True)
    total_variance_df = total_variance_df.append(df3, ignore_index=True)
    #print(sentrix_id, total_variance)
chaos_scores_df.index = chaos_scores_df["Sentrix_ID"]
del chaos_scores_df["Sentrix_ID"]
total_variance_df.index = total_variance_df["Sentrix_ID"]
del total_variance_df["Sentrix_ID"]
instability_results = pd.merge(chaos_scores_df,total_variance_df, left_index=True, right_index=True)
instability_results.iloc[:]

/var/folders/zg/syv6h0t100jg9zg1v37mf4nr0000gn/T/ipykernel_23154/3005241942.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  chaos_scores_df = chaos_scores_df.append(df2, ignore_index=True)
/var/folders/zg/syv6h0t100jg9zg1v37mf4nr0000gn/T/ipykernel_23154/3005241942.py:19: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  total_variance_df = total_variance_df.append(df3, ignore_index=True)
/var/folders/zg/syv6h0t100jg9zg1v37mf4nr0000gn/T/ipykernel_23154/3005241942.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  chaos_scores_df = chaos_scores_df.append(df2, ignore_index=True)
/var/folders/zg/syv6h0t100jg9zg1v37mf4nr0000gn/T/ipykernel_23154/3005241942.py:19: FutureWarning: The frame.append method is deprecated and will be

Chaos_Score  Total_Variance
Sentrix_ID                            
X10007               4        0.427730
X10011              14        3.722436
X10052             108       12.820095
X10091             177       27.327687
X10125             201       45.988924
...                ...             ...
X50214             259       59.415260
X50217             575      275.111538
X11479             586      196.581569
X11392             106       24.210618
X11426             557      175.219429

[103 rows x 2 columns]

# Export the results

In [14]:
# Export the results as a .csv
instability_results.to_csv("/Users/jenkinslab/Desktop/FAZSTProject/DNA_Damage_Project/Instability/HighComet_Instability_Results.csv")